In [7]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import glob, os, re, string
from datetime import datetime
from dateutil.parser import parse
from nltk.tokenize import sent_tokenize, word_tokenize, RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from polyglot.detect import Detector
from wordcloud import WordCloud

In [8]:
FDIR = 'data/unclean/'

files = [file for file in glob.glob(FDIR + '*.csv')]
files

['data/unclean/twitter_phrase_taxi-booking.csv',
 'data/unclean/twitter_referral_grab-referral-code.csv',
 'data/unclean/twitter_str_grabcar.csv',
 'data/unclean/twitter_referral_grab-reward-points.csv',
 'data/unclean/play_grab.csv',
 'data/unclean/twitter_referral_grabrewards.csv',
 'data/unclean/twitter_others_Grabeats.csv',
 'data/unclean/gplay_grab.csv',
 'data/unclean/twitter_others_Grabpay.csv',
 'data/unclean/twitter_phrase_ride-cancellation.csv',
 'data/unclean/twitter_phrase_grabeats-grabpay.csv',
 'data/unclean/twitter_str_grabhitch.csv',
 'data/unclean/appstore_tada.csv',
 'data/unclean/appstore_grab.csv',
 'data/unclean/twitter_str_ride-hailing.csv',
 'data/unclean/reddit_merged.csv',
 'data/unclean/twitter_referral_grab-promo-codes.csv',
 'data/unclean/twitter_str_grabshare.csv',
 'data/unclean/play_tada.csv',
 'data/unclean/reddit_gojek_comments.csv',
 'data/unclean/twitter_referral_grab-refer-code.csv',
 'data/unclean/twitter_phrase_grabfoods.csv',
 'data/unclean/twitte

In [9]:
prefixes = ['fb', 'twitter', 'gplay']

files_grp = [[f for f in files if p in f] for p in prefixes]

files_grp

[['data/unclean/fb_groups.csv'],
 ['data/unclean/twitter_phrase_taxi-booking.csv',
  'data/unclean/twitter_referral_grab-referral-code.csv',
  'data/unclean/twitter_str_grabcar.csv',
  'data/unclean/twitter_referral_grab-reward-points.csv',
  'data/unclean/twitter_referral_grabrewards.csv',
  'data/unclean/twitter_others_Grabeats.csv',
  'data/unclean/twitter_others_Grabpay.csv',
  'data/unclean/twitter_phrase_ride-cancellation.csv',
  'data/unclean/twitter_phrase_grabeats-grabpay.csv',
  'data/unclean/twitter_str_grabhitch.csv',
  'data/unclean/twitter_str_ride-hailing.csv',
  'data/unclean/twitter_referral_grab-promo-codes.csv',
  'data/unclean/twitter_str_grabshare.csv',
  'data/unclean/twitter_referral_grab-refer-code.csv',
  'data/unclean/twitter_phrase_grabfoods.csv',
  'data/unclean/twitter_str_ryde.csv',
  'data/unclean/twitter_str_ridesharing.csv',
  'data/unclean/twitter_referral_grab-promo.csv',
  'data/unclean/twitter_phrase_grab-taxi-ride.csv',
  'data/unclean/twitter_othe

In [2]:
def add_lang(df, col_name):
    detect_lang = lambda comment: Detector(str(comment), quiet=True).languages[0]

    df['lang_code'] = df.apply(lambda row: detect_lang(row[col_name]).code, axis=1)
    df['lang_sig'] = df.apply(lambda row: detect_lang(row[col_name]).confidence, axis=1)
    
    return df

In [3]:
def analyse_sentiment_vader(df, col_name):
    sid = SentimentIntensityAnalyzer()
    vader = lambda text: sid.polarity_scores(text)
    
    df['vader'] = df[col_name].apply(vader)
    df = pd.merge(df, df['vader'].apply(pd.Series), left_index=True, right_index=True)
    return df.drop(['vader'], axis=1)

In [19]:
df_fb = pd.read_csv('data/ca_unclean/grab/fb_hitchsg.csv',names=['url','date','comment'])
df_fb['date'] = df_fb['date'].apply(lambda x: parse(str(x)))
df_fb = df_fb[['date','comment']]
df_fb.head(20)

date                                            comment
0  2018-11-17 18:00:00  There still be ego,cheapo riders who think 5 c...
1  2018-11-17 18:00:00  there will be ego people around... just pray u...
2  2018-11-17 18:00:00  Till today there are riders that think as long...
3  2018-11-16 15:13:00  Thk you for sharing n showing what all need to...
4  2018-11-16 15:13:00                                         Martin Lau
5  2018-11-16 15:13:00  Nice article. Perhaps Grab should incentivise ...
6  2018-11-17 18:00:00                                          yishun???
7  2018-11-17 18:00:00  That's provided there is a driver who wants to...
8  2018-11-17 18:00:00                            $5 still wanna share.. 
9  2018-11-17 18:00:00                                  Cheapo to the max
10 2018-11-17 18:00:00       Knn micron staff all very rich yet so cheapo
11 2018-11-17 18:00:00                          Blacklist this cheapskate
12 2018-11-17 18:00:00                     Like that also can innovativev
13 2018-11-17 18:00:00  Only sorhai will pick up. I believe this notic...
14 2018-11-17 18:00:00                                         Ban micron
15 2018-11-17 18:00:00  It could be driver lo... Cuz no need to pay 10...
16 2018-11-17 18:00:00             Omg....really no word to describe.....
17 2018-11-17 18:00:00                                      Take bus lah.
18 2018-11-17 18:00:00                                                 附近
19 2018-11-17 18:00:00  No hitch driver will take 4pax in the rush hou...

In [20]:
df_fb = add_lang(df_fb, 'comment')
df_fb.head(10)

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

date                                            comment  \
0 2018-11-17 18:00:00  There still be ego,cheapo riders who think 5 c...   
1 2018-11-17 18:00:00  there will be ego people around... just pray u...   
2 2018-11-17 18:00:00  Till today there are riders that think as long...   
3 2018-11-16 15:13:00  Thk you for sharing n showing what all need to...   
4 2018-11-16 15:13:00                                         Martin Lau   
5 2018-11-16 15:13:00  Nice article. Perhaps Grab should incentivise ...   
6 2018-11-17 18:00:00                                          yishun???   
7 2018-11-17 18:00:00  That's provided there is a driver who wants to...   
8 2018-11-17 18:00:00                            $5 still wanna share..    
9 2018-11-17 18:00:00                                  Cheapo to the max   

  lang_code  lang_sig  
0        en      99.0  
1        en      98.0  
2        en      99.0  
3        en      98.0  
4        to      91.0  
5        en      99.0  
6        qu      87.0  
7        en      98.0  
8        en      94.0  
9        en      94.0

In [22]:
df_fb[df_fb['lang_code'] == 'en'].to_csv('data/ca_cleaned/grab/fb_grab_hitchsg.csv')

In [26]:
df_fb.dtypes

date         datetime64[ns]
comment              object
lang_code            object
lang_sig            float64
dtype: object

In [30]:
df_fb[df_fb['date'] > '2018-11-16']

date                                            comment  \
0   2018-11-17 18:00:00  There still be ego,cheapo riders who think 5 c...   
1   2018-11-17 18:00:00  there will be ego people around... just pray u...   
2   2018-11-17 18:00:00  Till today there are riders that think as long...   
3   2018-11-16 15:13:00  Thk you for sharing n showing what all need to...   
4   2018-11-16 15:13:00                                         Martin Lau   
5   2018-11-16 15:13:00  Nice article. Perhaps Grab should incentivise ...   
6   2018-11-17 18:00:00                                          yishun???   
7   2018-11-17 18:00:00  That's provided there is a driver who wants to...   
8   2018-11-17 18:00:00                            $5 still wanna share..    
9   2018-11-17 18:00:00                                  Cheapo to the max   
10  2018-11-17 18:00:00       Knn micron staff all very rich yet so cheapo   
11  2018-11-17 18:00:00                          Blacklist this cheapskate   
12  2018-11-17 18:00:00                     Like that also can innovativev   
13  2018-11-17 18:00:00  Only sorhai will pick up. I believe this notic...   
14  2018-11-17 18:00:00                                         Ban micron   
15  2018-11-17 18:00:00  It could be driver lo... Cuz no need to pay 10...   
16  2018-11-17 18:00:00             Omg....really no word to describe.....   
17  2018-11-17 18:00:00                                      Take bus lah.   
18  2018-11-17 18:00:00                                                 附近   
19  2018-11-17 18:00:00  No hitch driver will take 4pax in the rush hou...   
30  2018-11-16 15:03:00  Err..the telco which suitable for aunty and Un...   
31  2018-11-16 15:03:00  Just take Singtel combo 3? Unlimited talk time...   
32  2018-11-16 15:03:00  i got riders who replied to my sms via wa.. sa...   
33  2018-11-16 15:03:00                                    iMessage. Free.   
34  2018-11-16 15:03:00                                        $5.35cents?   
35  2018-11-16 15:03:00  sign up for recurring bill payment under starh...   
36  2018-11-16 15:03:00  As a StarHub Mobile subscriber, you can enjoy ...   
37  2018-11-16 15:03:00                                                NaN   
38  2018-11-16 15:03:00                 My SMS is unlimited and underused!   
39  2018-11-16 15:03:00                          Dun sms lo. Call instead.   
..                  ...                                                ...   
46  2018-11-16 15:03:00  For Starhub plans...if you pay with monthly re...   
47  2018-11-16 15:03:00                       Top up $3/month for 500 sms    
48  2018-11-16 15:03:00  I have written to Grab to include other msg se...   
49  2018-11-16 15:03:00  Thanks to all boys and girls for the helpful i...   
62  2018-11-16 11:24:00  Move on loh. Next time call them up after u ac...   
63  2018-11-16 11:24:00  Just search for the word "cancel" in GHC and u...   
64  2018-11-16 11:24:00                                     what u expect?   
65  2018-11-16 11:24:00  If the person so nice to ask u charges accordi...   
66  2018-11-16 11:24:00  Dun hor. Ask the person transfer to your accou...   
67  2018-11-16 11:24:00                                         Upset: Can   
68  2018-11-16 11:24:00          It's a trap to cause you your job/license   
69  2018-11-16 11:24:00  Very command mark them and never to pick them ...   
70  2018-11-16 11:24:00  Hehe... you are a real newbie... you need to g...   
71  2018-11-16 11:24:00  Just move on, kena once and never pick the guy...   
72  2018-11-16 11:24:00                    You are one of the  lucky one..   
73  2018-11-16 11:24:00  Just make sure you still drop off at the speci...   
74  2018-11-16 11:24:00                                      just move on~   
75  2018-11-16 11:24:00                        Charge them accordingly lah   
76  2018-11-16 11:24:00  If they ask u to charge them then go ahead but...   
77  2018-11-16 11:24:00                  

In [9]:
df_fb = add_lang(df_fb, 'comment')
df_fb = analyse_sentiment_vader(df_fb[df_fb['lang_code'] == 'en'], 'comment')

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [10]:
df_fb.head(20)

url                date  \
0   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
1   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
2   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
3   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-16 15:13:00   
5   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-16 15:13:00   
7   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
8   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
9   https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
10  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
11  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
12  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
13  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
15  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
16  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
17  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
19  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-17 18:00:00   
20  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-15 13:12:00   
21  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-15 13:12:00   
22  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-15 13:12:00   
23  https://m.facebook.com/groups/hitchsg?view=per... 2018-11-15 13:12:00   

                                              comment lang_code  lang_sig  \
0   There still be ego,cheapo riders who think 5 c...        en      99.0   
1   there will be ego people around... just pray u...        en      98.0   
2   Till today there are riders that think as long...        en      99.0   
3   Thk you for sharing n showing what all need to...        en      98.0   
5   Nice article. Perhaps Grab should incentivise ...        en      99.0   
7   That's provided there is a driver who wants to...        en      98.0   
8                             $5 still wanna share..         en      94.0   
9                                   Cheapo to the max        en      94.0   
10       Knn micron staff all very rich yet so cheapo        en      97.0   
11                          Blacklist this cheapskate        en      96.0   
12                     Like that also can innovativev        en      96.0   
13  Only sorhai will pick up. I believe this notic...        en      98.0   
15  It could be driver lo... Cuz no need to pay 10...        en      98.0   
16             Omg....really no word to describe.....        en      96.0   
17                                      Take bus lah.        en      92.0   
19  No hitch driver will take 4pax in the rush hou...        en      99.0   
20  that the risk u take,,,n did not missed ur fli...        en      98.0   
21  half story, it is good if everything turns out...        en      98.0   
22  I am also a grab hitch rider myself, yesterday...        en      99.0   
23  Actually if I wanted hitch for a flight at 7.5...        en      99.0   

      neg    neu    pos  compound  
0   0.000  0.832  0.168    0.6652  
1   0.000  0.839  0.161    0.3182  
2   0.104  0.896  0.000   -0.2023  
3   0.000  0.639  0.361    0.7767  
5   0.000  0.769  0.231    0.8126  
7   0.000  1.000  0.000    0.0000  
8   0.000  1.000  0.000    0.0000  
9   0.000  1.000  0.000    0.0000  
10  0.000  0.673  0.327    0.5984  
11  0.000  1.000  0.000    0.0000  
12  0.000  0.615  0.385    0.3612  
13  0.000  1.000  0.000    0.0000  
15  0.217  0.783  0.000   -0.3818  
16  0.355  0.645  0.000   -0.2960  
17  0.000  1.000  0.000    0.0000  
19  0.095  0.905  0.000   -0.2960  
20  0.191  0.637  0.172   -0.0547  
21  0.000  0.811  0.189    0.5040  
22  0.000  0.808  0.192    0.7085  
23  0.000  1.000  0.000    0.0000

In [14]:
df_fb = df_fb[['date', 'comment']]
df_fb['source'] = 'fb'
df_fb.to_csv('data/ca_cleaned/grab/fb_grab_hitchsg.csv')

In [15]:
df_comb = [pd.read_csv('data/ca_cleaned/grab_consolidated.csv'), pd.read_csv('data/ca_cleaned/grab/fb_grab_hitchsg.csv')]
df_new = pd.concat(df_comb)

In [16]:
df_new.head(25)

Unnamed: 0        date                                            comment  \
0           27  2018-11-02               More flexible for grabpay and top up   
1           34  2018-11-02  useful, easy to use, discount everyday,good se...   
2           36  2018-11-02                                             Thanks   
3           37  2018-11-02                                          Nice grab   
4           38  2018-11-02                                               Good   
5           39  2018-11-02  Grab has made my trips more enjoyable and stre...   
6           40  2018-11-02                        So far the service are good   
7           41  2018-11-02                                             Thanks   
8           42  2018-11-02  After I change the phone and reinstall again u...   
9           43  2018-11-02  the fees is getting expensive！dont make ppl ha...   
10          44  2018-11-02                                           Nice app   
11          45  2018-11-02                                               Slow   
12          46  2018-11-02                                               Good   
13          47  2018-11-02  can passengers refuse to ride when car arrived...   
14          48  2018-11-02                                               Easy   
15          49  2018-11-02  I am satisfied💟i love it keep it up yours serv...   
16          50  2018-11-02                  Take half an hour to load system.   
17          51  2018-11-02  Grab give me easy way to go . Price for grab i...   
18          52  2018-11-02             New app always crash. Wasting my time.   
19          53  2018-11-02             really useful and have good promotions   
20          54  2018-11-02                     So far so good to use this app   
21          55  2018-11-02                         Keep stopping after update   
22          56  2018-11-02      after updating apps often closed by itself...   
23          57  2018-11-02                                            Helpful   
24          58  2018-11-02            Perfect service more upgrade for future   

     source  
0     gplay  
1   twitter  
2   twitter  
3   twitter  
4   twitter  
5   twitter  
6   twitter  
7   twitter  
8   twitter  
9   twitter  
10  twitter  
11  twitter  
12  twitter  
13  twitter  
14  twitter  
15  twitter  
16  twitter  
17  twitter  
18  twitter  
19  twitter  
20  twitter  
21  twitter  
22  twitter  
23  twitter  
24  twitter

In [17]:
df_new.to_csv('data/ca_cleaned/grab_consolidated.csv')

In [ ]:
new_dir = 'data/en'

if not os.path.exists(new_dir):
    os.makedirs(new_dir)

In [11]:
files_grp[2][0][13:]

'gplay_grab.csv'

In [12]:
df_gp_grps = []

for f in files_grp[2]:
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    
    df = add_lang(df, 'comment')
    df['source'] = f[13:]
    df_gp_grps.append(df)

df_gp = pd.concat(df_gp_grps)
df_gp

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

name       date  rating  \
0                           A Google user 2018-11-02       5   
1                           A Google user 2018-11-02       1   
2                       Kumar Subramanian 2018-11-02       5   
3                           A Google user 2018-11-02       5   
4                           Zaky Mochamad 2018-11-02       2   
5                       Bernadette Alciso 2018-11-02       1   
6                             Bernd Bsser 2018-11-02       1   
7                          suryadi taufan 2018-11-02       5   
8                           A Google user 2018-11-02       5   
9                          ChenHoong Koon 2018-11-02       1   
10                 Achmad Rizki Dharmawan 2018-11-02       1   
11                           Putri Ardina 2018-11-02       4   
12                        Azizah Zuhairoh 2018-11-02       5   
13                         Saefudin Sardi 2018-11-02       5   
14                        Harshini Batchu 2018-11-02       1   
15                           Hazimi Aiman 2018-11-02       1   
16                            Waqas Saeed 2018-11-02       1   
17                            Tean Sim Ee 2018-11-02       2   
18                              Edward An 2018-11-02       1   
19                          A Google user 2018-11-02       1   
20                           Evan Sidarta 2018-11-02       1   
21                              Wawa Aziz 2018-11-02       2   
22                        Camille Sanchez 2018-11-02       2   
23                          A Google user 2018-11-02       5   
24                         Seiddy Shafiee 2018-11-02       2   
25                              Tobi Sama 2018-11-02       1   
26                            chau yi hua 2018-11-02       1   
27                              CHen cHeN 2018-11-02       3   
28   Gabrielle Immanuel Osvaldo Kurniawan 2018-11-02       5   
29                            Flower Girl 2018-11-02       1   
..                                    ...        ...     ...   
539                      Debashis Debnath 2015-10-01       4   
540                               Irfan A 2015-09-18       3   
541                        deathstryke 17 2015-09-17       2   
542                           Jayson Cena 2015-08-17       3   
543                            sally siow 2015-08-16       5   
544                       Andrei Jedidiah 2015-08-15       1   
545                        Muhammed Sadiq 2015-08-13       1   
546                              phlanx18 2015-08-07       4   
547                         syafiq syahmi 2015-08-01       1   
548                            Thomas Ong 2015-06-30       5   
549                              Scorp Ho 2015-06-23       1   
550                            Chester Wu 2015-06-20       1   
551                              Darcy Li 2015-06-13       1   
552                          Amy Lijia Ma 2015-05-28       5   
553                             Zhao Yang 2015-05-28       5   
554                              Andy Teo 2015-05-22       1   
555                            Josh Ching 2015-05-20       1   
556                           aaron moses 2015-05-10       5   
557                           Christmin K 2015-05-07       1   
558                            Evonne Peh 2015-05-04       2   
559                         Alphonsus Tan 2015-03-28       5   
560                              John Lui 2015-03-26       3   
561                            Skee Thong 2015-03-26       5   
562                                   E C 2015-03-26       1   
563                               Amy Ang 2015-03-25       1   
564                              Air Pork 2015-03-07       5   
565                           Amanda Wong 2015-02-10       5   
566                           Terence Zou 2015-02-04       5   
567                            Alwin Chan 2015-02-04       5   
568                              Ming Tan 2015-02-02       5   

                                               comment lang_code  la

In [18]:
df_tw_grps = []

for f in files_grp[1]:
    df = pd.read_csv(f)
    df['tweet'] = df['tweet'].apply(lambda row: ''.join([x for x in str(row) if x in string.printable]))
    df = add_lang(df, 'tweet')
    df['source'] = f[13:]
    df_tw_grps.append(df)

df_tw = pd.concat(df_tw_grps)

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [16]:
df_fb = pd.read_csv(files_grp[0][0], encoding='utf-8')
df_fb = add_lang(df_fb, 'comment')
df_fb['source'] = f[13:]

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [20]:
df_lang_grps = [df_gp[['lang_code','lang_sig']],df_tw[['lang_code','lang_sig']],df_fb[['lang_code','lang_sig']]]

df_lang = pd.concat(df_lang_grps)
df_lang.head(20)

lang_code  lang_sig
0         en      96.0
1         en      99.0
2         en      96.0
3         en      94.0
4         en      99.0
5         en      96.0
6         en      99.0
7         en      90.0
8         en      97.0
9         en      96.0
10        id      99.0
11        id      99.0
12        en      83.0
13        en      94.0
14        en      98.0
15        en      94.0
16        en      94.0
17        ht      80.0
18        en      99.0
19        en      97.0

In [21]:
df_lang.shape

(123080, 2)

In [28]:
df_lang['lang_code'].value_counts()

en         92476
id         14798
ms          4725
tl          3643
ht          1927
un          1126
nl           637
vi           267
da           252
de           215
ceb          165
sk           117
jw           117
fr            90
th            88
nn            86
aa            83
lt            83
ga            83
es            81
sco           78
kha           77
sw            68
war           56
so            53
tlh           53
sv            52
ts            50
su            48
br            47
           ...  
ig             8
kl             8
oc             8
mfe            7
ny             7
crs            7
vo             7
mi             6
ja             6
km             6
nso            6
zh_Hant        5
co             5
fo             5
ca             4
xx_Qaai        4
ar             4
az             3
ss             2
ik             2
bs             2
ru             2
el             1
ne             1
sd             1
ko             1
ta             1
zu            

In [5]:
for f in files_gp:
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    
    df = add_lang(df, 'comment')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:], encoding='utf-8')

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [19]:
for f in files_tw:
    df = pd.read_csv(f)
    df = add_lang(df, 'tweet')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:])

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

error: ('input contains invalid UTF-8 around byte 44 (of 78)', 'occurred at index 904')

In [28]:
for f in files_fb:
    df = pd.read_csv(f, encoding='utf-8')
    df = add_lang(df, 'comment')
    
    df[df['lang_code'] == 'en'].to_csv(new_dir + '/' + f[5:], encoding='utf-8')

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

In [29]:
def process_google_play(f):
    gp_head = ['name', 'date', 'rating', 'comment']
    df = pd.read_csv(f, names=gp_head, encoding='utf-8')
    df['date'] = pd.to_datetime(df['date'])
    df['source'] = f[5:]
    
    return add_lang(df, 'comment')

gp_list = [process_google_play(f) for f in files_gp]

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to dete

AttributeError: 'list' object has no attribute 'concat'

In [30]:
gp_all = pd.concat(gp_list)
gp_all.to_csv(new_dir + '/' + 'gplay_consolidated.csv')
gp_all[gp_all['lang_code'] == 'en'].to_csv(new_dir + '/' + 'gplay_consolidated_en.csv')

In [5]:
def process_twitter(f):
    df = pd.read_csv(f, encoding='iso-8859-1')
    return add_lang(df, 'tweet')

tw_list = [process_twitter(f) for f in files_tw]

error: ('input contains invalid UTF-8 around byte 2 (of 173)', 'occurred at index 3')

In [37]:
tw_all = pd.concat(tw_list)
tw_all.to_csv(new_dir + '/' + 'twitter_consolidated.csv')
tw_all[tw_all['lang_code'] == 'en'].to_csv(new_dir + '/' + 'twitter_consolidated_en.csv')

NameError: name 'tw_list' is not defined